<a href="https://colab.research.google.com/github/taggartpatrick/basic_bike_sales_analytics/blob/main/Bike_Sales_Basic_EDA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Load libraries


In [1]:
# Load basic libraries
import pandas as pd
import numpy as np
import altair as alt
import datetime as dt

In [2]:
# load pandas profiling 
import sys

!{sys.executable} -m pip install -U pandas-profiling[notebook]
!jupyter nbextension enable --py widgetsnbextension

import pandas_profiling

     |████████████████████████████████| 245kB 5.7MB/s 
     |████████████████████████████████| 81kB 10.2MB/s 
     |████████████████████████████████| 604kB 24.3MB/s 
     |████████████████████████████████| 61kB 8.8MB/s 
     |████████████████████████████████| 81kB 10.3MB/s 
     |████████████████████████████████| 3.1MB 18.7MB/s 
     |████████████████████████████████| 112kB 49.0MB/s 
     |████████████████████████████████| 296kB 46.8MB/s 
  Created wheel for htmlmin: filename=htmlmin-0.1.12-cp36-none-any.whl size=27085 sha256=2f011cadda7b03e18429f21003c74f311a5d5472d92b552d7f98e2a32fe9360f
  Stored in directory: /root/.cache/pip/wheels/43/07/ac/7c5a9d708d65247ac1f94066cf1db075540b85716c30255459
  Created wheel for phik: filename=phik-0.11.0-cp36-none-any.whl size=599738 sha256=6b70302d5b1ad4a5a800966254c5a4fe70868783a0024642b621f0251c3e7b57
  Stored in directory: /root/.cache/pip/wheels/af/54/11/aba77f21075918de02f7964eabfe8c10d5542df9e6ad10b225
Successfully built htmlmin phik
ERROR: g

In [3]:
# load interactive tables
%load_ext google.colab.data_table

In [4]:
# load plotly 
!pip install -q plotly==4.2.1
import plotly.graph_objects as go

from IPython.display import HTML
import plotly.express as px

     |████████████████████████████████| 7.2MB 3.7MB/s 


In [5]:
# load seaborn libraries 
import seaborn as sns
import matplotlib.pyplot as plt 

### Import data


#### Import data from Github repo

In [6]:
# Clone Github directory
!git clone https://github.com/taggartpatrick/basic_bike_sales_analytics
!ls

Cloning into 'basic_bike_sales_analytics'...
remote: Enumerating objects: 23, done.
remote: Counting objects: 100% (23/23), done.
remote: Compressing objects: 100% (21/21), done.
remote: Total 23 (delta 7), reused 0 (delta 0), pack-reused 0
Unpacking objects: 100% (23/23), done.
basic_bike_sales_analytics  sample_data


In [7]:
# Import ordeline data 
orderlines = pd.read_excel("/content/basic_bike_sales_analytics/orderlines.xlsx")

# Import bikeshop data 
bikeshops = pd.read_excel("/content/basic_bike_sales_analytics/bikeshops.xlsx")

# Import bike data 
bikes = pd.read_excel("/content/basic_bike_sales_analytics/bikes.xlsx")

In [8]:
# Import bike orderline data 
bike_orderlines = pd.read_csv("/content/basic_bike_sales_analytics/bike_orderlines.csv")

### Tidy and Transform Bike Sales Data

#### Combine Excel Files into one dataframe

In [9]:
# Rename key fields in relevant excel based dataframes for merging

bikes = bikes.rename(columns = {'bike.id':'product.id'})
bikeshops = bikeshops.rename(columns = {'bikeshop.id': 'customer.id'})

# Join dataframes into one overall dataframe

bike_order_data = pd.merge(orderlines,bikes, on = 'product.id')
bike_order_data = pd.merge(bike_order_data,bikeshops, on = 'customer.id')

#### Tidy Dataframe

In [10]:
# Rename key fields
bike_sales_tbl = bike_order_data.rename(columns = {
    'order.date' : 'order_date',
    'order.id' : 'order_id',
    'order.line' : 'order_line',
    'bikeshop.name':'bikeshop_name'
    })

# Drop uneeded fields 
bike_sales_tbl = bike_sales_tbl.drop(['Unnamed: 0','customer.id','product.id'], axis = 1) 

# Split location fields and split decsription fields 
bike_sales_tbl[['major_category','minor_category','frame_material']] = bike_sales_tbl['description'].str.split(' - ',2,expand = True)

# Add fields for month, day and year

def get_ym(x): return dt.datetime(x.year,x.month,1)

bike_sales_tbl['order_month'] = pd.DatetimeIndex(bike_sales_tbl['order_date']).month
bike_sales_tbl['order_day'] = pd.DatetimeIndex(bike_sales_tbl['order_date']).day
bike_sales_tbl['order_year'] = pd.DatetimeIndex(bike_sales_tbl['order_date']).year
bike_sales_tbl['order_ym'] = bike_sales_tbl['order_date'].apply(get_ym)
bike_sales_tbl['order_weekday'] = pd.to_datetime(bike_sales_tbl['order_date']).dt.day_name()

# Add total sales value 
bike_sales_tbl['sales_value'] = bike_sales_tbl['price']*bike_sales_tbl['quantity']

### Perform Initial EDA 

#### View full table and data profile

In [11]:
# view dataframe information
bike_sales_tbl.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 15644 entries, 0 to 15643
Data columns (total 18 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   order_id        15644 non-null  int64         
 1   order_line      15644 non-null  int64         
 2   order_date      15644 non-null  datetime64[ns]
 3   quantity        15644 non-null  int64         
 4   model           15644 non-null  object        
 5   description     15644 non-null  object        
 6   price           15644 non-null  int64         
 7   bikeshop_name   15644 non-null  object        
 8   location        15644 non-null  object        
 9   major_category  15644 non-null  object        
 10  minor_category  15644 non-null  object        
 11  frame_material  15644 non-null  object        
 12  order_month     15644 non-null  int64         
 13  order_day       15644 non-null  int64         
 14  order_year      15644 non-null  int64         
 15  or

In [12]:
# View bike sales table
bike_sales_tbl.head()

order_id  order_line order_date  ...   order_ym order_weekday sales_value
0         1           1 2011-01-07  ... 2011-01-01        Friday        6070
1       132           6 2011-05-13  ... 2011-05-01        Friday        6070
2       507           2 2012-06-26  ... 2012-06-01       Tuesday        6070
3       528          18 2012-07-16  ... 2012-07-01        Monday        6070
4       691          13 2013-02-05  ... 2013-02-01       Tuesday        6070

[5 rows x 18 columns]

In [13]:
# View bike sales insights
report = bike_sales_tbl.profile_report(
    sort="None", html={"style": {"full_width": True}}, progress_bar=False
)
report

#### Group Sales by Shop

In [14]:
# Get sales by bikeshop
shop_sales = bike_sales_tbl.groupby('bikeshop_name')['sales_value'].sum().to_frame(name = "Total Sales").reset_index()

In [15]:
shop_sales

bikeshop_name  Total Sales
0             Albuquerque Cycles      1002880
1                Ann Arbor Speed      1973910
2                Austin Cruisers       688885
3               Cincinnati Speed      1859035
4        Columbus Race Equipment      1767005
5                  Dallas Cycles       681080
6               Denver Bike Shop      7697670
7                 Detroit Cycles      1637845
8       Indianapolis Velocipedes       941005
9       Ithaca Mountain Climbers      6299335
10             Kansas City 29ers     11535455
11              Las Vegas Cycles      3073615
12            Los Angeles Cycles       962050
13     Louisville Race Equipment      1934800
14          Miami Race Equipment      2057130
15         Minneapolis Bike Shop      2023220
16            Nashville Cruisers      1072925
17       New Orleans Velocipedes      2761825
18               New York Cycles      1374625
19  Oklahoma City Race Equipment      3450040
20        Philadelphia Bike Shop       774550
21               Phoenix Bi-peds      4168535
22  Pittsburgh Mountain Machines      1755420
23              Portland Bi-peds      1972130
24            Providence Bi-peds      1625710
25         San Antonio Bike Shop       573655
26        San Francisco Cruisers      1640470
27        Seattle Race Equipment       375895
28                   Tampa 29ers       971245
29                 Wichita Speed      2380385

In [16]:
# Bar chart of sales
source = shop_sales

bars = alt.Chart(source).mark_bar().encode(
    x="Total Sales",
    y= alt.Y("bikeshop_name",sort='-x'),
    tooltip = ['Total Sales']
)

text = bars.mark_text(
    align='left',
    baseline='middle',
    dx=3  # Nudges text to right so it doesn't appear on top of the bar
).encode(
    text='Total Sales'
)

(bars + text).properties(height=900)

alt.LayerChart(...)

#### Get Sales by Bike Frame over time

In [17]:
# Get Sales over time by frame material
sales_mat_tbl = bike_sales_tbl.groupby(['frame_material','order_ym'])['sales_value'].sum().reset_index()

sales_mat_tbl

frame_material   order_ym  sales_value
0         Aluminum 2011-01-01       127295
1         Aluminum 2011-02-01       345595
2         Aluminum 2011-03-01       145415
3         Aluminum 2011-04-01       538430
4         Aluminum 2011-05-01       287730
..             ...        ...          ...
115         Carbon 2015-08-01       638090
116         Carbon 2015-09-01       559190
117         Carbon 2015-10-01       706750
118         Carbon 2015-11-01       759610
119         Carbon 2015-12-01       689970

[120 rows x 3 columns]

In [18]:
# produce facet plot by Material 
source = sales_mat_tbl

line = alt.Chart(source).mark_line().encode(
    x = 'order_ym',
    y = 'sales_value',
    color = 'frame_material',
    tooltip = ['order_ym', 'sales_value']
).properties(
    width = 300,
    height = 300
).facet(column = 'frame_material')
line


alt.FacetChart(...)

#### Plot Price vs Qty by Bike Model 

#### Get Qty vs Price by Bike model and major category



In [19]:
#Produce table of qty, price and major category
qty_price_majcat_tbl = bike_sales_tbl.groupby(['model','major_category']).agg(
    {'price':'mean',
     'quantity':'sum',
     'sales_value': 'sum'}).reset_index()


qty_price_majcat_tbl

model major_category  price  quantity  sales_value
0           Bad Habit 1       Mountain   3200       253       809600
1           Bad Habit 2       Mountain   2660       218       579880
2   Beast of the East 1       Mountain   2770       269       745130
3   Beast of the East 2       Mountain   2130       243       517590
4   Beast of the East 3       Mountain   1620       217       351540
..                  ...            ...    ...       ...          ...
92              Trail 5       Mountain    815       262       213530
93     Trigger Carbon 1       Mountain   8200       164      1344800
94     Trigger Carbon 2       Mountain   5970       168      1002960
95     Trigger Carbon 3       Mountain   3730       211       787030
96     Trigger Carbon 4       Mountain   3200       258       825600

[97 rows x 5 columns]

In [20]:
#Show qty vs price & overall sales by major category in altair

source = bike_sales_tbl.groupby(['model','major_category']).agg(
    {'price':'mean',
     'quantity':'sum',
     'sales_value': 'sum'}
     ).reset_index()

line = alt.Chart(source).mark_point().encode(
    x='quantity',
    y='price',
    size = 'sales_value',
    color = 'major_category',
    tooltip=['model', 'quantity','price','sales_value']
).properties(
    width = 400, 
    height = 300
    ).facet(column = 'major_category').interactive()

line

alt.FacetChart(...)

#### View Matrix of Qty by Model with Sales History overlaid

In [21]:
# Create a table that contains bike model, total_qty, price, order_ym, qty ordered 
model_price_qty_tbl = bike_sales_tbl.groupby(['model']).agg({'price': 'mean',
                                                         'quantity' : 'sum'}).reset_index()

# Create table of sales history by quanity
qty_hist_tbl = bike_sales_tbl.groupby(['model','order_ym'])['quantity'].sum().to_frame(name = 'monthly_quantity').reset_index()

# Merge the above tables to create a composite table
full_tbl = pd.merge(model_price_qty_tbl,qty_hist_tbl, on = 'model')

full_tbl

model  price  quantity   order_ym  monthly_quantity
0          Bad Habit 1   3200       253 2011-01-01                 1
1          Bad Habit 1   3200       253 2011-02-01                 7
2          Bad Habit 1   3200       253 2011-03-01                 1
3          Bad Habit 1   3200       253 2011-04-01                 9
4          Bad Habit 1   3200       253 2011-05-01                 4
...                ...    ...       ...        ...               ...
5212  Trigger Carbon 4   3200       258 2015-06-01                 5
5213  Trigger Carbon 4   3200       258 2015-07-01                 4
5214  Trigger Carbon 4   3200       258 2015-08-01                 2
5215  Trigger Carbon 4   3200       258 2015-10-01                 4
5216  Trigger Carbon 4   3200       258 2015-11-01                 3

[5217 rows x 5 columns]

In [22]:
model_price_qty_tbl

model  price  quantity
0           Bad Habit 1   3200       253
1           Bad Habit 2   2660       218
2   Beast of the East 1   2770       269
3   Beast of the East 2   2130       243
4   Beast of the East 3   1620       217
..                  ...    ...       ...
92              Trail 5    815       262
93     Trigger Carbon 1   8200       164
94     Trigger Carbon 2   5970       168
95     Trigger Carbon 3   3730       211
96     Trigger Carbon 4   3200       258

[97 rows x 3 columns]

In [23]:
model_list = ['Bad Habit 1','Bad Habit 2','Beast of the East 1']

data = full_tbl[full_tbl['model'].isin(model_list)]

In [24]:
# Produce complex time series plot

alt.data_transformers.disable_max_rows()

data = full_tbl

selector = alt.selection_single(empty='all', fields=['model'])

base = alt.Chart(data).properties(
    width=500,
    height=250
).add_selection(selector)

points = base.mark_point(filled=True, size=200).encode(
    x='quantity',
    y='price',
    color=alt.condition(selector, 'model:O', alt.value('lightgray'), legend=None),
)

timeseries = base.mark_line().encode(
    x='order_ym',
    y=alt.Y('monthly_quantity', scale=alt.Scale(domain=(-15, 15))),
    color=alt.Color('model:O', legend=None)
).transform_filter(
    selector
)

points | timeseries

alt.HConcatChart(...)

### Write files to csv

Write files to google drive


In [25]:
from google.colab import drive
drive.mount('/gdrive')
bike_sales_tbl.to_csv("/gdrive/MyDrive/Colab Notebooks/Raw Data Files/bike sales table.csv")

Mounted at /gdrive
